In [1]:
#Importa as bibliotecas necessárias
import pandas as pd
import numpy as np
import random
from datetime import timedelta

In [2]:
#Cria uma base fictícia de colaboradores, representados por suas matrículas únicas
base_ficticia = pd.DataFrame()
base_ficticia['matricula'] = [random.randint(100,999) for i in range (1000)]
base_ficticia.drop_duplicates(subset='matricula', inplace = True)

In [3]:
#Cria os setores e canais fictícios de atendimento ao cliente. Em nosso exemplo, teremos oito setores e quatro canais de atendimento
setores = {1:'Setor A', 2:'Setor B', 3:'Setor C',4:'Setor D',
          5:'Setor E',6:'Setor F',7:'Setor G',8:'Setor H'}

canais = {1:'Chat', 2:'E-mail', 
          3:'Telefone',4:'WhatsApp'}

#Uma lista com horários de entrada, de 0:00 a 23:00, será criada. Para reproduzir melhor o mundo real, foi atribuído peso maior aos horários entre 06:00 e 18:00, peso
#médio aos horários entre 19:00 e 23:00 e um menor peso aos horários entre 00:00 e 05:00. Isso foi feito apenas repetindo o número de vezes em que cada horário,
#aparece na lista 3, 2 e 1 vezes, respectivamente. Assim, tem-se uma lista com 55 elementos, e o fator aleatório levará isso em consideração
entradas = [str(i)+':00' for i in range(0,6)] + 3*[str(i)+':00' for i in range(6,19)] + 2*[str(i)+':00' for i in range(19,24)]

horarios_entradas = {}

for i, entrada in enumerate(entradas):
  horarios_entradas[i] = entrada

In [4]:
#Inclui um setor, um canal e uma entrada fictícios para cada colaborador
base_ficticia['setor'] = [setores[random.randint(1,8)] for i in range(len(base_ficticia))]
base_ficticia['canal'] = [canais[random.randint(1,4)] for i in range(len(base_ficticia))]
base_ficticia['entrada'] = [horarios_entradas[random.randint(0,54)] for i in range(len(base_ficticia))]

In [5]:
#Distribuição entre os setores
base_ficticia.setor.value_counts()

Setor F    82
Setor G    78
Setor A    78
Setor H    75
Setor C    75
Setor D    74
Setor E    70
Setor B    61
Name: setor, dtype: int64

In [6]:
#Distribuição entre os canais
base_ficticia.canal.value_counts()

Chat        160
WhatsApp    158
Telefone    143
E-mail      132
Name: canal, dtype: int64

In [7]:
#Distribuição entre os horários de entrada
base_ficticia.entrada.value_counts()

15:00    43
7:00     39
18:00    35
17:00    35
13:00    34
11:00    33
6:00     33
20:00    32
12:00    32
16:00    30
14:00    30
8:00     29
9:00     26
21:00    22
10:00    21
19:00    20
23:00    17
22:00    16
3:00     14
1:00     13
0:00     13
5:00     11
4:00     10
2:00      5
Name: entrada, dtype: int64

In [8]:
#Ilustração da base fictícia
base_ficticia.head()

matricula    setor     canal entrada
0        709  Setor B      Chat    9:00
1        492  Setor F  Telefone   13:00
2        845  Setor A    E-mail    8:00
3        540  Setor E  WhatsApp   20:00
4        413  Setor F    E-mail   15:00

In [9]:
#Converte os horários de entrada de string para datetime
base_ficticia.entrada = base_ficticia.entrada.apply(lambda entrada: pd.to_datetime(entrada))

In [10]:
#Cria uma função para definir o horário da primeira pausa. O critério utilizado foi o resto da divisão do index de cada colaborador (após segmentar cada setor
#canal e horário de entrada, aplica-se um reset_index()) por 4, já que tem-se a obrigatoriedade de se dividir os colaboradores em no máximo 4 grupos para o
#desfrute das pausas. Cada grupo realizará suas pausas exatamente 10 min após o grupo imediatamente anterior
def primeira_pausa(entrada, indice):
  if (indice/4 - indice//4) == 0.0:
    primeira_pausa = entrada + timedelta(seconds = 3600)
  elif (indice/4 - indice//4) == 0.25:
    primeira_pausa = entrada + timedelta(seconds = 4200)
  elif (indice/4 - indice//4) == 0.50:
    primeira_pausa = entrada + timedelta(seconds = 4800)
  else:
    primeira_pausa = entrada + timedelta(seconds = 5400)
  
  return primeira_pausa

#Segue a lógica da função criada acima, porém agora se atentando ao fato de pausas não poderem ser usufruídas na última hora de trabalho
def terceira_pausa(entrada, indice):
  if (indice/4 - indice//4) == 0.0:
    primeira_pausa = entrada + timedelta(seconds = 16800)
  elif (indice/4 - indice//4) == 0.25:
    primeira_pausa = entrada + timedelta(seconds = 17400)
  elif (indice/4 - indice//4) == 0.50:
    primeira_pausa = entrada + timedelta(seconds = 18000)
  else:
    primeira_pausa = entrada + timedelta(seconds = 18600)
  
  return primeira_pausa

#Cria o que será o resultado final da escala de pausas, em formato dataframe
df_final = pd.DataFrame()

#Itera sobre os setores
for setor in base_ficticia.setor.unique():
  #Seleciona apenas o setor desejado
  df_setor = base_ficticia[base_ficticia.setor == setor]
  
  #Itera sobre os canais
  for canal in df_setor.canal.unique():
    #Seleciona apenas o canal desejado
    df_canal = df_setor[df_setor.canal == canal]
    
    #Itera sobre os horários de entrada
    for entrada in df_canal.entrada.unique():
      #Seleciona apenas o horário de entrada desejado
      df_entrada = df_canal[df_canal.entrada == entrada]

      #Deixa o dataframe resultante com o index adequado à aplicação das funções criadas anteriormente
      df_entrada.reset_index(drop = True,inplace=True)
      
      #Define os horários para a primeira pausa, com utilização da função 'primeira_pausa'
      df_entrada['1ª Pausa'] = list(map(primeira_pausa,list(df_entrada['entrada']),list(df_entrada.index)))
      #Define os horários para a segunda pausa, de forma equivalente para todos os colaboradores: 01:40 após a primeira pausa
      df_entrada['2ª Pausa'] = df_entrada['1ª Pausa'].apply(lambda pausa: pausa + timedelta(seconds = 6000))
      #Define os horários para a terceira pausa, com utilização da função 'terceira_pausa'
      df_entrada['3ª Pausa'] = list(map(terceira_pausa,list(df_entrada['entrada']),list(df_entrada.index)))
      #Define o horário de saída, 06:20 após o horário de entrada
      df_entrada['saida'] = df_entrada['entrada'].apply(lambda pausa: pausa + timedelta(seconds = 22800))

      #Unifica o que já foi gerado com o dataframe atual
      df_final = pd.concat([df_final,df_entrada])

<ipython-input-10-b064b0d7705c>:51: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_entrada['1ª Pausa'] = list(map(primeira_pausa,list(df_entrada['entrada']),list(df_entrada.index)))
<ipython-input-10-b064b0d7705c>:53: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_entrada['2ª Pausa'] = df_entrada['1ª Pausa'].apply(lambda pausa: pausa + timedelta(seconds = 6000))
<ipython-input-10-b064b0d7705c>:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[

In [11]:
#Classifica o dataframe resultante de acordo com os critérios de horário de entrada, setor e canal, respectivamente
df_final.sort_values(by=['entrada','setor','canal'],inplace=True)

#Converte as colunas em que constam horários para o timpo time
for i in range(3,8):
  df_final.iloc[:,i] = df_final.iloc[:,i].apply(lambda datetime: datetime.time())

In [12]:
#Ilustração da escala de pausas resultante
df_final

matricula    setor     canal   entrada  1ª Pausa  2ª Pausa  3ª Pausa  \
0         283  Setor A      Chat  00:00:00  01:00:00  02:40:00  04:40:00   
0         157  Setor A    E-mail  00:00:00  01:00:00  02:40:00  04:40:00   
0         740  Setor B      Chat  00:00:00  01:00:00  02:40:00  04:40:00   
0         751  Setor B    E-mail  00:00:00  01:00:00  02:40:00  04:40:00   
0         903  Setor C  WhatsApp  00:00:00  01:00:00  02:40:00  04:40:00   
..        ...      ...       ...       ...       ...       ...       ...   
1         920  Setor F  Telefone  23:00:00  00:10:00  01:50:00  03:50:00   
0         329  Setor G  Telefone  23:00:00  00:00:00  01:40:00  03:40:00   
0         228  Setor H    E-mail  23:00:00  00:00:00  01:40:00  03:40:00   
0         232  Setor H  Telefone  23:00:00  00:00:00  01:40:00  03:40:00   
0         882  Setor H  WhatsApp  23:00:00  00:00:00  01:40:00  03:40:00   

       saida  
0   06:20:00  
0   06:20:00  
0   06:20:00  
0   06:20:00  
0   06:20:00  
..       ...  
1   05:20:00  
0   05:20:00  
0   05:20:00  
0   05:20:00  
0   05:20:00  

[593 rows x 8 columns]